# Using LightFM to Create Hybrid Model

As we've seen in our last two modeling sections both models add some value the the recommender system. However, a few issues with the ones before is that content-based doesn't take in mind how others have rated items, only shows us very similar items and therefore we aren't introduced to new items. And with collaborative-fitering we need have a very sparce data set, because most users have not interacted/rated these items. 

So, by combining the two we can overcome these issues. This hybrid method applies both techniques into one.

Next Steps:
1. read in the data and properlly format it
.......

#### Read in the needed libraries:

In [1]:
import pandas as pd
import numpy as np
import spacy
import pickle
from Mod_5_functions import (pickle_file,open_pickle,in_nyc,is_sample,return_lemma,replace_fixed_words)

from lightfm.datasets import fetch_stackexchange

data = fetch_stackexchange('crossvalidated',
                           test_set_fraction=0.1,
                           indicator_features=False,
                           tag_features=True)

train = data['train']
test = data['test']


/Users/elenasm7/anaconda/lib/python3.6/site-packages/lightfm/_lightfm_fast.py:9: UserWarning: LightFM was compiled without OpenMP support. Only a single thread will be used.
  warnings.warn('LightFM was compiled without OpenMP support. '


#### Read in the data sets:

In [2]:
from sklearn.metrics.pairwise import cosine_similarity

training_df_cats = open_pickle('Data/training_df_with_categories')

training_df_cats.dropna(inplace=True)
# sklearn.metrics.pairwise.cosine_similarity(X, Y=None, dense_output=True)

In [3]:
training_df_cats.reset_index(drop=True,inplace=True)

In [4]:
training_df_cats.columns

Index(['comapny_source', 'company_loc', 'rev_comp_rating', 'rev_comp_reviews',
       'rev_comp_url', 'rev_company_name', 'userUrl', 'word_count',
       'char_count', 'numerics', 'upper', 'bangs', 'stp_wrd_cnt',
       'rev_comp_reviews_corrections_new', 'new_rating', 'rev_comp_id',
       'categories', 'ids', 'rating', 'review_count'],
      dtype='object')

In [5]:
CF_df = training_df_cats[['userUrl','rev_comp_id','rev_comp_rating']]
CB_df = training_df_cats[['userUrl','rev_comp_id','categories']]

# training_df_cats.columns

In [6]:
from tqdm._tqdm_notebook import tqdm_notebook

tqdm_notebook.pandas(desc="Progress: ")

CB_df.categories = CB_df.categories.progress_apply(lambda cats: ' '.join(cats))

/Users/elenasm7/anaconda/lib/python3.6/site-packages/pandas/core/generic.py:3643: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self[name] = value


In [7]:
CB_df.drop_duplicates(inplace=True)

/Users/elenasm7/anaconda/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [8]:
CB_df.reset_index(inplace=True,drop=True)

In [12]:
CB_df.categories.shape

(11186,)

In [ ]:
CB_df.userUrl

In [9]:
from sklearn.feature_extraction.text import TfidfVectorizer
vec = TfidfVectorizer(ngram_range=(0,3))
tfidf_matrix = vec.fit_transform(CB_df.categories)

cosine_similarities = cosine_similarity(tfidf_matrix,Y=None,dense_output=False)

In [14]:
results_2 = {} 
for idx, row in set_user_cats_train.iterrows(): #iterates through all the rows
    similar_zip = sorted(list(zip(cosine_similarities[idx].indices,cosine_similarities[idx].data)),key=lambda tup: tup[1], reverse=True)
    similar_indices = [i[0] for i in sorted(similar_zip,key = lambda tupe: tupe[1], reverse=True)]
    similar_items = [CB_df['rev_comp_id'][i] for i in similar_indices]
    sim_score = [i[1] for i in similar_zip]
    results_2[row['rev_comp_id'] = list(zip(similar_items,sim_score))

In [44]:
results_2 = {} 
similar_zip = sorted(list(zip(cosine_similarities[0].indices,cosine_similarities[0].data)),key=lambda tup: tup[1], reverse=True)
similar_indices = [i[0] for i in sorted(similar_zip,key = lambda tupe: tupe[1], reverse=True)]
similar_items = [CB_df['rev_comp_id'][i] for i in similar_indices]
sim_score = [i[1] for i in similar_zip]
results_2[CB_df['rev_comp_id'][0]] = list(zip(similar_items,sim_score))

In [45]:
results_2

{'planet-fitness-manhattan-canal-st-ny-new-york': [('blink-fitness-canarsie-brooklyn',
   1.0),
  ('blink-fitness-murray-hill-new-york', 1.0),
  ('blink-fitness-canarsie-brooklyn', 1.0),
  ('blink-fitness-canarsie-brooklyn', 1.0),
  ('blink-fitness-canarsie-brooklyn', 1.0),
  ('blink-fitness-sheepshead-bay-brooklyn-2', 1.0),
  ('bally-sport-jamaica', 1.0),
  ('blink-fitness-murray-hill-new-york', 1.0),
  ('new-york-sports-clubs-brooklyn-12', 1.0),
  ('planet-fitness-brooklyn-flatbush-new-york', 1.0),
  ('planet-fitness-brooklyn-rockaway-ave-brooklyn', 1.0),
  ('tribeca-heath-and-fitness-new-york', 1.0),
  ('planet-fitness-brooklyn-rockaway-ave-brooklyn', 1.0),
  ('blink-fitness-penn-station-new-york', 1.0),
  ('blink-fitness-noho-new-york', 1.0),
  ('24-hour-fitness-sheepshead-bay-brooklyn', 1.0),
  ('24-hour-fitness-sheepshead-bay-brooklyn', 1.0),
  ('new-york-sports-clubs-brooklyn-13', 1.0),
  ('24-hour-fitness-sheepshead-bay-brooklyn', 1.0),
  ('24-hour-fitness-sheepshead-bay-brookl

(11180, 1.0)

In [16]:
print(cosine_similarities)

  (0, 11185)	0.7377018972137657
  (0, 11184)	0.19528525159251786
  (0, 11183)	0.33922363186755894
  (0, 11182)	0.33282347993949485
  (0, 11181)	1.0
  (0, 11180)	1.0
  (0, 11179)	1.0
  (0, 11178)	1.0
  (0, 11177)	1.0
  (0, 11176)	0.5905544974870905
  (0, 11175)	1.0
  (0, 11174)	0.1825073039804262
  (0, 11173)	0.6244822257738699
  (0, 11172)	0.1825073039804262
  (0, 11171)	0.3111905143169398
  (0, 11170)	0.7053335471505715
  (0, 11169)	0.7053335471505715
  (0, 11168)	0.7053335471505715
  (0, 11167)	0.23379333416277218
  (0, 11166)	0.7053335471505715
  (0, 11165)	0.7053335471505715
  (0, 11164)	0.23390343040166614
  (0, 11163)	0.7053335471505715
  (0, 11162)	0.7053335471505715
  (0, 11161)	1.0
  :	:
  (11185, 24)	0.25668060544412397
  (11185, 23)	0.6206050161861965
  (11185, 22)	0.36324186493519967
  (11185, 21)	0.3996504307159988
  (11185, 20)	0.3025500442750686
  (11185, 19)	0.47088590552927284
  (11185, 18)	0.5144125505281099
  (11185, 17)	0.3996504307159988
  (11185, 16)	0.12690647560

In [55]:
# cosine_similarities_2 = cosine_similarity(CF_df,Y=None,dense_output=False)
CF_df.head()

userUrl  \
0  https://www.yelp.com/user_details?userid=exPhu...   
1  https://www.yelp.com/user_details?userid=exPhu...   
2  https://www.yelp.com/user_details?userid=exPhu...   
3  https://www.yelp.com/user_details?userid=exPhu...   
4  https://www.yelp.com/user_details?userid=exPhu...   

                                         rev_comp_id  rev_comp_rating  
0      planet-fitness-manhattan-canal-st-ny-new-york              3.0  
1                         montauk-salt-cave-new-york              2.0  
2  pure-barre-new-york-columbus-circle-60th-and-b...              3.0  
3  return-to-life-center-pilates-and-functional-m...              4.0  
4                                   peloton-new-york              4.0

In [ ]:
# ratings_df = pd.pivot_table(CF_df, index='userUrl', columns='rev_comp_id', aggfunc=np.max)
ratings_df.loc['https://www.yelp.com/user_details?userid=-03y31IzykunU9azzgLsoQ']

In [61]:
ratings_df.sum()

                 rev_comp_id                                           
rev_comp_rating  14th-street-y-new-york                                     15.0
                 21-pilates-new-york-2                                      15.0
                 212-pilates-new-york                                        5.0
                 22nd-street-synergy-fitness-new-york                        8.0
                 24-hour-fitness-53rd-st-new-york                           71.0
                 24-hour-fitness-bay-shore-bay-shore                         1.0
                 24-hour-fitness-bensonhurst-brooklyn                       17.0
                 24-hour-fitness-broadway-and-houston-ultra-new-york        41.0
                 24-hour-fitness-jamaica-center-jamaica                      3.0
                 24-hour-fitness-kew-gardens-kew-gardens                     4.0
                 24-hour-fitness-kings-highway-brooklyn                      7.0
                 24-hour-fitness-litt

In [99]:
new_cos_mat = cosine_similarities.todense()

In [101]:
new_cos_mat.shape

(11186, 11186)

In [64]:
CB_df.categories

0                          gyms healthtrainers
1                       halotherapy reiki yoga
2                                 barreclasses
3                         barreclasses pilates
4           cyclingclasses gyms healthtrainers
5                                         yoga
6        yoga meditationcenters healthretreats
7                 cyclingclasses cardioclasses
8                       spas yoga barreclasses
9                                 barreclasses
10                           meditationcenters
11                   yoga barreclasses pilates
12                                barreclasses
13                                barreclasses
14                             cafes yoga bars
15           gyms healthtrainers cardioclasses
16            golf golfcartrentals golflessons
17          cyclingclasses gyms healthtrainers
18                                        gyms
19                                        yoga
20                                pilates yoga
21          c

In [46]:
# 1.142727250064263
import surprise
from surprise import BaselineOnly
from surprise.model_selection import GridSearchCV
from surprise.reader import Reader
from surprise import Dataset

reader = Reader(rating_scale=(1, 5))
data = Dataset.load_from_df(CF_df, reader)
# bsl_options= {'method': 'sgd', 'reg': 0.08, 'learning_rate': 0.01, 'n_epocha': 3}
# algo = BaselineOnly(bsl_options=bsl_options)
# predictions = algo.fit(data).test(data)
# accuracy.rmse(predictions)

In [47]:
param_grid = {'bsl_options': {'method': ['sgd'],
                              'reg': [0.02,0.03,0.04],
                             'learning_rate':[0.0055,0.0065,0.01,0.02],
                             'n_epocha':[5,7,10]}}
gs = GridSearchCV(BaselineOnly, param_grid, cv=10)
# ['n_epochs': [5,10,15], 'reg_u': [10,15,20],'reg_i': [5,10,15],
gs.fit(data)

# best RMSE score
print(gs.best_score['rmse'])

# combination of parameters that gave the best RMSE score
print(gs.best_params['rmse'])

Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimati

Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Estimati

In [48]:
algo = gs.best_estimator['rmse']
algo.fit(data.build_full_trainset())

Estimating biases using sgd...


In [52]:
CF_df.columns

Index(['userUrl', 'rev_comp_id', 'rev_comp_rating'], dtype='object')

In [67]:
# both_lists =[list(set(CF_df.userUrl)),list(set(CF_df.rev_comp_id))]
# import itertools
# # for i in users[:1]:
# #     for j in companies[0]:
# #         print(i,j)
# result = list(itertools.product(*both_lists))
len(result)

5936944

In [85]:
user_comp_rating = {}
count = 0
for pair in result:
    print(f'just did {count}')
    user_comp_rating[pair] = algo.predict(pair[0], pair[1])[3]
    count+= 1

just did 0
just did 1
just did 2
just did 3
just did 4
just did 5
just did 6
just did 7
just did 8
just did 9
just did 10
just did 11
just did 12
just did 13
just did 14
just did 15
just did 16
just did 17
just did 18
just did 19
just did 20
just did 21
just did 22
just did 23
just did 24
just did 25
just did 26
just did 27
just did 28
just did 29
just did 30
just did 31
just did 32
just did 33
just did 34
just did 35
just did 36
just did 37
just did 38
just did 39
just did 40
just did 41
just did 42
just did 43
just did 44
just did 45
just did 46
just did 47
just did 48
just did 49
just did 50
just did 51
just did 52
just did 53
just did 54
just did 55
just did 56
just did 57
just did 58
just did 59
just did 60
just did 61
just did 62
just did 63
just did 64
just did 65
just did 66
just did 67
just did 68
just did 69
just did 70
just did 71
just did 72
just did 73
just did 74
just did 75
just did 76
just did 77
just did 78
just did 79
just did 80
just did 81
just did 82
just did 83
ju

just did 638
just did 639
just did 640
just did 641
just did 642
just did 643
just did 644
just did 645
just did 646
just did 647
just did 648
just did 649
just did 650
just did 651
just did 652
just did 653
just did 654
just did 655
just did 656
just did 657
just did 658
just did 659
just did 660
just did 661
just did 662
just did 663
just did 664
just did 665
just did 666
just did 667
just did 668
just did 669
just did 670
just did 671
just did 672
just did 673
just did 674
just did 675
just did 676
just did 677
just did 678
just did 679
just did 680
just did 681
just did 682
just did 683
just did 684
just did 685
just did 686
just did 687
just did 688
just did 689
just did 690
just did 691
just did 692
just did 693
just did 694
just did 695
just did 696
just did 697
just did 698
just did 699
just did 700
just did 701
just did 702
just did 703
just did 704
just did 705
just did 706
just did 707
just did 708
just did 709
just did 710
just did 711
just did 712
just did 713
just did 714

just did 1249
just did 1250
just did 1251
just did 1252
just did 1253
just did 1254
just did 1255
just did 1256
just did 1257
just did 1258
just did 1259
just did 1260
just did 1261
just did 1262
just did 1263
just did 1264
just did 1265
just did 1266
just did 1267
just did 1268
just did 1269
just did 1270
just did 1271
just did 1272
just did 1273
just did 1274
just did 1275
just did 1276
just did 1277
just did 1278
just did 1279
just did 1280
just did 1281
just did 1282
just did 1283
just did 1284
just did 1285
just did 1286
just did 1287
just did 1288
just did 1289
just did 1290
just did 1291
just did 1292
just did 1293
just did 1294
just did 1295
just did 1296
just did 1297
just did 1298
just did 1299
just did 1300
just did 1301
just did 1302
just did 1303
just did 1304
just did 1305
just did 1306
just did 1307
just did 1308
just did 1309
just did 1310
just did 1311
just did 1312
just did 1313
just did 1314
just did 1315
just did 1316
just did 1317
just did 1318
just did 1319
just d

just did 1834
just did 1835
just did 1836
just did 1837
just did 1838
just did 1839
just did 1840
just did 1841
just did 1842
just did 1843
just did 1844
just did 1845
just did 1846
just did 1847
just did 1848
just did 1849
just did 1850
just did 1851
just did 1852
just did 1853
just did 1854
just did 1855
just did 1856
just did 1857
just did 1858
just did 1859
just did 1860
just did 1861
just did 1862
just did 1863
just did 1864
just did 1865
just did 1866
just did 1867
just did 1868
just did 1869
just did 1870
just did 1871
just did 1872
just did 1873
just did 1874
just did 1875
just did 1876
just did 1877
just did 1878
just did 1879
just did 1880
just did 1881
just did 1882
just did 1883
just did 1884
just did 1885
just did 1886
just did 1887
just did 1888
just did 1889
just did 1890
just did 1891
just did 1892
just did 1893
just did 1894
just did 1895
just did 1896
just did 1897
just did 1898
just did 1899
just did 1900
just did 1901
just did 1902
just did 1903
just did 1904
just d

just did 2419
just did 2420
just did 2421
just did 2422
just did 2423
just did 2424
just did 2425
just did 2426
just did 2427
just did 2428
just did 2429
just did 2430
just did 2431
just did 2432
just did 2433
just did 2434
just did 2435
just did 2436
just did 2437
just did 2438
just did 2439
just did 2440
just did 2441
just did 2442
just did 2443
just did 2444
just did 2445
just did 2446
just did 2447
just did 2448
just did 2449
just did 2450
just did 2451
just did 2452
just did 2453
just did 2454
just did 2455
just did 2456
just did 2457
just did 2458
just did 2459
just did 2460
just did 2461
just did 2462
just did 2463
just did 2464
just did 2465
just did 2466
just did 2467
just did 2468
just did 2469
just did 2470
just did 2471
just did 2472
just did 2473
just did 2474
just did 2475
just did 2476
just did 2477
just did 2478
just did 2479
just did 2480
just did 2481
just did 2482
just did 2483
just did 2484
just did 2485
just did 2486
just did 2487
just did 2488
just did 2489
just d

...

just did 507375
just did 507376
just did 507377
just did 507378
just did 507379
just did 507380
just did 507381
just did 507382
just did 507383
just did 507384
just did 507385
just did 507386
just did 507387
just did 507388
just did 507389
just did 507390
just did 507391
just did 507392
just did 507393
just did 507394
just did 507395
just did 507396
just did 507397
just did 507398
just did 507399
just did 507400
just did 507401
just did 507402
just did 507403
just did 507404
just did 507405
just did 507406
just did 507407
just did 507408
just did 507409
just did 507410
just did 507411
just did 507412
just did 507413
just did 507414
just did 507415
just did 507416
just did 507417
just did 507418
just did 507419
just did 507420
just did 507421
just did 507422
just did 507423
just did 507424
just did 507425
just did 507426
just did 507427
just did 507428
just did 507429
just did 507430
just did 507431
just did 507432
just did 507433
just did 507434
just did 507435
just did 507436
just did

just did 508086
just did 508087
just did 508088
just did 508089
just did 508090
just did 508091
just did 508092
just did 508093
just did 508094
just did 508095
just did 508096
just did 508097
just did 508098
just did 508099
just did 508100
just did 508101
just did 508102
just did 508103
just did 508104
just did 508105
just did 508106
just did 508107
just did 508108
just did 508109
just did 508110
just did 508111
just did 508112
just did 508113
just did 508114
just did 508115
just did 508116
just did 508117
just did 508118
just did 508119
just did 508120
just did 508121
just did 508122
just did 508123
just did 508124
just did 508125
just did 508126
just did 508127
just did 508128
just did 508129
just did 508130
just did 508131
just did 508132
just did 508133
just did 508134
just did 508135
just did 508136
just did 508137
just did 508138
just did 508139
just did 508140
just did 508141
just did 508142
just did 508143
just did 508144
just did 508145
just did 508146
just did 508147
just did

just did 508804
just did 508805
just did 508806
just did 508807
just did 508808
just did 508809
just did 508810
just did 508811
just did 508812
just did 508813
just did 508814
just did 508815
just did 508816
just did 508817
just did 508818
just did 508819
just did 508820
just did 508821
just did 508822
just did 508823
just did 508824
just did 508825
just did 508826
just did 508827
just did 508828
just did 508829
just did 508830
just did 508831
just did 508832
just did 508833
just did 508834
just did 508835
just did 508836
just did 508837
just did 508838
just did 508839
just did 508840
just did 508841
just did 508842
just did 508843
just did 508844
just did 508845
just did 508846
just did 508847
just did 508848
just did 508849
just did 508850
just did 508851
just did 508852
just did 508853
just did 508854
just did 508855
just did 508856
just did 508857
just did 508858
just did 508859
just did 508860
just did 508861
just did 508862
just did 508863
just did 508864
just did 508865
just did

just did 509635
just did 509636
just did 509637
just did 509638
just did 509639
just did 509640
just did 509641
just did 509642
just did 509643
just did 509644
just did 509645
just did 509646
just did 509647
just did 509648
just did 509649
just did 509650
just did 509651
just did 509652
just did 509653
just did 509654
just did 509655
just did 509656
just did 509657
just did 509658
just did 509659
just did 509660
just did 509661
just did 509662
just did 509663
just did 509664
just did 509665
just did 509666
just did 509667
just did 509668
just did 509669
just did 509670
just did 509671
just did 509672
just did 509673
just did 509674
just did 509675
just did 509676
just did 509677
just did 509678
just did 509679
just did 509680
just did 509681
just did 509682
just did 509683
just did 509684
just did 509685
just did 509686
just did 509687
just did 509688
just did 509689
just did 509690
just did 509691
just did 509692
just did 509693
just did 509694
just did 509695
just did 509696
just did

KeyboardInterrupt: 

In [73]:
algo.predict('https://www.yelp.com/user_details?userid=des-3-7ypCnTLOODi_FO8A','re-ab-pilates-new-york')

Prediction(uid='https://www.yelp.com/user_details?userid=des-3-7ypCnTLOODi_FO8A', iid='re-ab-pilates-new-york', r_ui=None, est=4.041952944379383, details={'was_impossible': False})

In [77]:
result[0]

('https://www.yelp.com/user_details?userid=des-3-7ypCnTLOODi_FO8A',
 're-ab-pilates-new-york')

In [83]:
algo.predict(result[0][0], result[0][1])[3]

4.041952944379383

In [92]:
sim_matrix = algo.compute_similarities()

Computing the msd similarity matrix...
Done computing similarity matrix.


In [103]:
sim_matrix

array([[1. , 1. , 0.5, ..., 0. , 0. , 0. ],
       [1. , 1. , 0.5, ..., 0. , 0. , 0. ],
       [0.5, 0.5, 1. , ..., 0. , 0. , 0. ],
       ...,
       [0. , 0. , 0. , ..., 1. , 1. , 0. ],
       [0. , 0. , 0. , ..., 1. , 1. , 0. ],
       [0. , 0. , 0. , ..., 0. , 0. , 1. ]])

In [102]:
CF_df.userUrl.shape

(11186,)

In [ ]:
def get_Iu(uid):
    """ return the number of items rated by given user
    args: 
      uid: the id of the user
    returns: 
      the number of items rated by the user
    """
    try:
        return len(trainset.ur[trainset.to_inner_uid(uid)])
    except ValueError: # user was not part of the trainset
        return 0
    
def get_Ui(iid):
    """ return number of users that have rated given item
    args:
      iid: the raw id of the item
    returns:
      the number of users that have rated the item.
    """
    try: 
        return len(trainset.ir[trainset.to_inner_iid(iid)])
    except ValueError:
        return 0
    
df = pd.DataFrame(predictions, columns=['uid', 'iid', 'rui', 'est', 'details'])
df['Iu'] = df.uid.apply(get_Iu)
df['Ui'] = df.iid.apply(get_Ui)
df['err'] = abs(df.est - df.rui)
best_predictions = df.sort_values(by='err')[:10]
worst_predictions = df.sort_values(by='err')[-10:]

In [105]:
from scipy.sparse import csr_matrix
new_train = csr_matrix(sim_matrix)

In [ ]:
from lightfm import LightFM

NUM_THREADS = 2
NUM_COMPONENTS = 30
NUM_EPOCHS = 3
ITEM_ALPHA = 1e-6

model = LightFM(loss='warp',
                item_alpha=ITEM_ALPHA,
                no_components=NUM_COMPONENTS)

# Fit the hybrid model. Note that this time, we pass
# in the item features matrix.
model = model.fit(new_train,
                item_features=cosine_similarities,
                epochs=NUM_EPOCHS,
                num_threads=NUM_THREADS)

In [ ]:
from sklearn.cluster import KMeans

kmeans = KMeans(n_clusters=10, random_state=0).fit(X)